In [ ]:
import csv
import json
from datetime import datetime, timedelta
import time

class HistoryProcessor:
    def __init__(self, csv_path, handler, clickhouse_client, period_seconds):
        self.csv_path = csv_path
        self.handler = handler
        self.db = clickhouse_client
        self.period = period_seconds

    def floor_to_period(self, unixts):
        # Найти начало интервала
        start = int(unixts // self.period * self.period)
        return start

    def run(self):
        with open(self.csv_path, "r") as f:
            reader = csv.reader(f)
            
            current_period = None
            first_cycle = True
            buffer_row = None

            for row in reader:
                try:
                    message = json.loads(row[0])
                    msg_ts = int(message["timestamp"])  # unixtimestamp
                except Exception as e:
                    continue # обработка ошибок парсинга

                if current_period is None:
                    # Ищем первый интервал, синхронизированный на начало минуты
                    current_period = self.floor_to_period(msg_ts)
                
                # Разделяем на временные окна, выбрасывая все что до первой "красивой" границы
                if first_cycle and (msg_ts < current_period):
                    continue  # сообщение до первого валидного окна
                first_cycle = False

                # Если сообщение попадает в текущее окно
                if msg_ts < current_period + self.period:
                    self.handler.on_message(message)
                else:
                    # Новый временной интервал
                    self.save_to_db(current_period)

                    # Передвигаем current_period на период вперед до "захвата" текущего сообщения
                    while msg_ts >= current_period + self.period:
                        current_period += self.period

                    self.handler.reset()  # опционально, если нужно очистить состояние между окнами
                    self.handler.on_message(message)

            # По завершении файла — финальный дамп, если был хоть один обработанный период
            if not first_cycle:
                self.save_to_db(current_period)

    def save_to_db(self, period_start):
        orderbook = self.handler.get_orderbook()
        # Пример вставки
        self.db.execute(
            'INSERT INTO orderbook_table (period_start, data) VALUES',
            [(period_start, json.dumps(orderbook))]
        )

# Пример инициализации:
# handler = MyOrderbookHandler()
# clickhouse = ... # Ваш ClickHouse client, например clickhouse-driver
# proc = HistoryProcessor("history.csv", handler, clickhouse, 15)
# proc.run()
